In [8]:
import multiprocessing
import time
%matplotlib inline
import IPython.display as ipd
import torch
from torch.utils.data import DataLoader

import commons
import utils
from data_utils import TextAudioSpeakerLoader, TextAudioSpeakerCollate
from models import SynthesizerTrn
from text import text_to_sequence
from text.symbols import symbols
from text.symbols import stressed_symbols
from scipy.io.wavfile import write
from dataset.test_sentences import master_thesis_test_sentences, long_sentence, very_long_sentence
import time

def get_text(text, hps):
    text_norm = text_to_sequence(text, hps.data.text_cleaners)
    if hps.data.add_blank:
        text_norm = commons.intersperse(text_norm, 0)
    text_norm = torch.LongTensor(text_norm)
    return text_norm

## LJ Speech

In [4]:
hps = utils.get_hparams_from_file("./configs/mif_base.json")

In [5]:
net_g = SynthesizerTrn(
    len(symbols),
    hps.data.filter_length // 2 + 1,
    hps.train.segment_size // hps.data.hop_length,
    **hps.model).cuda()
_ = net_g.eval()

_ = utils.load_checkpoint("/media/arnas/SSD Disk/uni/semester_3/master_thesis/repos/vits/logs/mif_base/G_629000.pth", net_g, None)

In [6]:
stn_tst = get_text("gal man pasakysite kas vyksta nes as nieko nesuprantu", hps)
with torch.no_grad():
    x_tst = stn_tst.cuda().unsqueeze(0)
    x_tst_lengths = torch.LongTensor([stn_tst.size(0)]).cuda()
    audio = net_g.infer(x_tst, x_tst_lengths, noise_scale=.667, noise_scale_w=0.8, length_scale=1)[0][0,0].data.cpu().float().numpy()
ipd.display(ipd.Audio(audio, rate=hps.data.sampling_rate, normalize=False))

## VCTK

In [ ]:
hps = utils.get_hparams_from_file("./configs/vctk_base.json")

In [ ]:
net_g = SynthesizerTrn(
    len(symbols),
    hps.data.filter_length // 2 + 1,
    hps.train.segment_size // hps.data.hop_length,
    n_speakers=hps.data.n_speakers,
    **hps.model).cuda()
_ = net_g.eval()

_ = utils.load_checkpoint("/path/to/pretrained_vctk.pth", net_g, None)

In [ ]:
stn_tst = get_text("VITS is Awesome!", hps)
with torch.no_grad():
    x_tst = stn_tst.cuda().unsqueeze(0)
    x_tst_lengths = torch.LongTensor([stn_tst.size(0)]).cuda()
    sid = torch.LongTensor([4]).cuda()
    audio = net_g.infer(x_tst, x_tst_lengths, sid=sid, noise_scale=.667, noise_scale_w=0.8, length_scale=1)[0][0,0].data.cpu().float().numpy()
ipd.display(ipd.Audio(audio, rate=hps.data.sampling_rate, normalize=False))

### Paulius TTS

In [2]:
hps = utils.get_hparams_from_file("./configs/mif_stressed.json")
# hps = utils.get_hparams_from_file("./configs/mif_base.json")

In [3]:
net_g = SynthesizerTrn(
    len(stressed_symbols),
    # len(symbols),
    hps.data.filter_length // 2 + 1,
    hps.train.segment_size // hps.data.hop_length,
    **hps.model).cuda()
_ = net_g.eval()

# _ = utils.load_checkpoint("/media/arnas/SSD Disk/uni/semester_3/master_thesis/repos/vits/logs/mif_base/G_1033000.pth", net_g, None)
# _ = utils.load_checkpoint("/media/arnas/SSD Disk/uni/semester_3/master_thesis/repos/vits/logs/mif_stressed/G_330000.pth", net_g, None)
_ = utils.load_checkpoint("/home/arnas/Downloads/logs/mif_base/G_615000.pth", net_g, None)

[2022-01-20 15:46:22,914] INFO:PID-145193:MainThread:utils: Loaded checkpoint '/home/arnas/Downloads/logs/mif_base/G_615000.pth' (iteration 151)


[INFO] Loaded checkpoint '/home/arnas/Downloads/logs/mif_base/G_615000.pth' (iteration 151)


In [4]:
output_dir = "/media/arnas/SSD Disk/uni/semester_3/master_thesis/mtd-files/audio/paulius/vits-paulius-stressed-common"
sentences = master_thesis_test_sentences['common_sentences']
sentences_filenames = master_thesis_test_sentences['common_sentences_filenames']

sentences_filenames = ['_'.join(name.split()[:8]) for name in sentences_filenames]

In [10]:
# stn_tst = get_text("išeikite į lauką, pasukite į kairę ir eikite tiesiai iki pastato galo. Jūsų ieškoma įstaiga bus jums iš dešinės. Užeikite, eikite tiesiai iki salės galo, pasukite į kairę ir iškvieskite liftą. Kilkite į aštuntą aukštą. Kompanija bus koridoriaus gale.", hps)
# stn_tst = get_text("Kažkaip man sunkiai sekasi kalbėti", hps)
# stn_tst = get_text("Labas vakaras, kaip laikaisi?", hps)
# stn_tst = get_text("Išeìkite į laùką, pasùkite į kaìrę ir̃ eĩkite tiésiai ikì pástato gálo.", hps)
# stn_tst = get_text("Išeikite į lauką, pasukite į kairę ir eikite tiesiai iki pastato galo.", hps)

sentence_idx = 3
stn_tst = get_text(long_sentence, hps)
# stn_tst = get_text(sentences[sentence_idx], hps)
start_time = time.time()
with torch.no_grad():
    x_tst = stn_tst.cuda().unsqueeze(0)
    x_tst_lengths = torch.LongTensor([stn_tst.size(0)]).cuda()
    audio = net_g.infer(x_tst, x_tst_lengths, noise_scale=.667, noise_scale_w=0.8, length_scale=1)[0][0,0].data.cpu().float().numpy()
print("Synthesis duration:", time.time() - start_time)
ipd.display(ipd.Audio(audio, rate=hps.data.sampling_rate, normalize=False))

Synthesis duration: 1.8162565231323242


In [19]:
write(f"/home/arnas/Downloads/save_apmokantys_algoritmai1.wav", 22050, audio)
# write(f"{output_dir}/{sentences_filenames[sentence_idx]}.wav", 22050, audio)

### Voice Conversion

In [ ]:
dataset = TextAudioSpeakerLoader(hps.data.validation_files, hps.data)
collate_fn = TextAudioSpeakerCollate()
num_cpus = multiprocessing.cpu_count()
loader = DataLoader(dataset, num_workers=num_cpus, shuffle=False,
    batch_size=1, pin_memory=True,
    drop_last=True, collate_fn=collate_fn)
data_list = list(loader)

In [ ]:
with torch.no_grad():
    x, x_lengths, spec, spec_lengths, y, y_lengths, sid_src = [x.cuda() for x in data_list[0]]
    sid_tgt1 = torch.LongTensor([1]).cuda()
    sid_tgt2 = torch.LongTensor([2]).cuda()
    sid_tgt3 = torch.LongTensor([4]).cuda()
    audio1 = net_g.voice_conversion(spec, spec_lengths, sid_src=sid_src, sid_tgt=sid_tgt1)[0][0,0].data.cpu().float().numpy()
    audio2 = net_g.voice_conversion(spec, spec_lengths, sid_src=sid_src, sid_tgt=sid_tgt2)[0][0,0].data.cpu().float().numpy()
    audio3 = net_g.voice_conversion(spec, spec_lengths, sid_src=sid_src, sid_tgt=sid_tgt3)[0][0,0].data.cpu().float().numpy()
print("Original SID: %d" % sid_src.item())
ipd.display(ipd.Audio(y[0].cpu().numpy(), rate=hps.data.sampling_rate, normalize=False))
print("Converted SID: %d" % sid_tgt1.item())
ipd.display(ipd.Audio(audio1, rate=hps.data.sampling_rate, normalize=False))
print("Converted SID: %d" % sid_tgt2.item())
ipd.display(ipd.Audio(audio2, rate=hps.data.sampling_rate, normalize=False))
print("Converted SID: %d" % sid_tgt3.item())
ipd.display(ipd.Audio(audio3, rate=hps.data.sampling_rate, normalize=False))
